In [1]:
import time
from selenium import webdriver
import pandas as pd
from geopy.geocoders import Nominatim
import folium
from time import sleep
import json
from folium import Marker
from folium.plugins import MarkerCluster
import numpy as np
from scipy import stats
import haversine as hs
import matplotlib.pyplot as plt

### 스마트해법 지점 위치 데이터 크롤링

In [2]:
driver = webdriver.Edge()

list1 = []

for i in range(287248, 289544):
    # 검색어 입력 및 검색
    review_search_url = f"https://www.smarthb-math.co.kr/franchise/find.php?ptype=view&idx={i}"

    driver.get(review_search_url)

    name = driver.find_element(by='xpath',value = f'//*[@id="wrap"]/div[3]/div/table/tbody/tr[1]/th').text # 지점명
    address = driver.find_element(by='xpath',value = f'//*[@id="wrap"]/div[3]/div/table/tbody/tr[2]/td').text # 주소

    list1.append([i, name, address])

    df = pd.DataFrame(list1)
    df.to_csv('./data/해법수학.csv')
    time.sleep(0.1)

In [2]:
hb=pd.read_csv('./data/해법수학.csv',index_col = 0)

In [3]:
hb

0            1                                        2
0     287248          효천점        전북 전주시 완산구 효천중앙로 57 (효자동2가, 모악빌딩)
1     287249     효천우미린2차점                       전북 전주시 완산구 효천서로 20
2     287250      효천연세수학점                       전북 전주시 완산구 효천서로 20
3     287251        효자포스코                       전북 전주시 완산구 봉곡로 132
4     287252     효자세븐팰리스점   전북 전주시 완산구 호암로 75-11 (효자동2가, 7단지아파트상가)
...      ...          ...                                      ...
2291  289539      sk view  서울 영등포구 여의대방로35가길 19 (신길동, 보라매 SK VIEW)
2292  289540   DMC스마트해법학원                   서울 서대문구 증가로 150 (남가좌동)
2293  289541  스마트해법수학 왕지점            전남 순천시 연동남길 39 (조례동, 서영옥머리마당)
2294  289542   스마트해법 북아현점                      서울 서대문구 북아현동 180-27
2295  289543  수원 광교SK레이크점  경기 수원시 영통구 법조로 25 (하동, 광교 SK VIEW Lake)

[2296 rows x 3 columns]

#### 데이터 전처리

In [4]:
hb.drop(columns = '0', inplace = True)

In [5]:
hb.rename(columns = {'1' : 'name' , '2' : 'address'}, inplace = True)

In [6]:
hb['address2'] = 0

In [7]:
for i in range(0,len(hb)):
    hb.loc[i,'address2'] = hb['address'][i].split('(')[-1]

In [8]:
for i in range(0,len(hb)):
    hb.loc[i,'address'] = hb['address'][i].split('(')[0]

In [9]:
hb.head(10)

name                 address              address2
0       효천점    전북 전주시 완산구 효천중앙로 57           효자동2가, 모악빌딩)
1  효천우미린2차점      전북 전주시 완산구 효천서로 20    전북 전주시 완산구 효천서로 20
2   효천연세수학점      전북 전주시 완산구 효천서로 20    전북 전주시 완산구 효천서로 20
3     효자포스코      전북 전주시 완산구 봉곡로 132    전북 전주시 완산구 봉곡로 132
4  효자세븐팰리스점   전북 전주시 완산구 호암로 75-11       효자동2가, 7단지아파트상가)
5     효자문학점  전북 전주시 완산구 유연로 217-11   효자동3가, 호반베르디움아파트 상가)
6  효자골든팰리스점      전북 전주시 완산구 호암로 40   효자동2가, 골든팰리스휴먼시아아파트)
7  화천 사내교실점    강원 화천군 사내면 포화로 1142                   사창리)
8    화일 캠퍼스       서울 강서구 까치산로4길 50                   화곡동)
9   화성지사직영점        경기 화성시 동탄기흥로 557      경기 화성시 동탄기흥로 557

### 위치 정보를 위도, 경도로 바꾸기

In [158]:
def geocoding(address):
    geolocoder = Nominatim(user_agent = 'South Korea', timeout=None)
    geo = geolocoder.geocode(address)
    address = {"lat": str(geo.latitude), "lng": str(geo.longitude)}

    return address

In [159]:
list_locate = []

for i in range(0,len(hb)):
    while 1:
        try:
            address = geocoding(hb.loc[i,'address'])
            list_locate.append([hb.loc[i,'name'], hb.loc[i,'address'], address['lat'],address['lng']])
            print(hb.loc[i,'name'], hb.loc[i,'address'],address['lat'], address['lng'])

            locate = pd.DataFrame(list_locate)

            locate.to_csv('./data/hb.csv')
            break

        except:
            hb.loc[i,'address'] = hb.loc[i,'address'][:-1]

            if hb.loc[i,'address'] == '':
                print('주소를 찾지 못했습니다')
                break

In [10]:
hb = pd.read_csv('./data/hb.csv')

In [11]:
hb

name                address   latitude   longitude
0             효천점   전북 전주시 완산구 효천중앙로 57   35.798765  127.105030
1        효천우미린2차점     전북 전주시 완산구 효천서로 20  35.801031  127.103024
2         효천연세수학점     전북 전주시 완산구 효천서로 20  35.801031  127.103024
3           효자포스코            전북 전주시 완산구   35.812200  127.119700
4        효자세븐팰리스점           전북 전주시 완산구 호  35.815756  127.153523
...           ...                    ...        ...         ...
2291      sk view  서울 영등포구 여의대방로35가길 19   37.501930  126.917541
2292   DMC스마트해법학원       서울 서대문구 증가로 150   37.570576  126.930506
2293  스마트해법수학 왕지점        전남 순천시 연동남길 39   34.956071  127.534327
2294   스마트해법 북아현점    서울 서대문구 북아현동 180-27  37.559472  126.955249
2295  수원 광교SK레이크점     경기 수원시 영통구 법조로 25   37.288190  127.066229

[2296 rows x 4 columns]

In [162]:
competitor = pd.read_csv('./data/competitor.csv',index_col = 0)

In [163]:
competitor.columns = ['address']

In [ ]:
list_locate = []

for i in range(0,len(competitor)):
    while 1:
        try:
            add = geocoding(competitor.loc[i,'address'])
            list_locate.append([competitor.loc[i,'address'], add['lat'],add['lng']])
            print(competitor.loc[i,'address'],add['lat'], add['lng'])

            locate = pd.DataFrame(list_locate)

            locate.to_csv('/data/competitor_locate.csv')
            break

        except:
            competitor.loc[i,'address'] = competitor.loc[i,'address'][:-1]

            if competitor.loc[i,'address'] == '':
                print('주소를 찾지 못했습니다')
                break

충청북도 청주 36.6421169 127.4891742
충청북도 청주시 흥덕구 가경로 123 한국 36.6193814 127.4423722


In [ ]:
competitor = pd.read_csv('./data/competitor_locate.csv',index_col = 0)

### 지도

In [12]:
m = folium.Map(
    location = [ 36.5 , 128 ],
    tiles = 'cartodbpositron',
    zoom_start = 7)

In [13]:
mc = MarkerCluster()

### 스마트해법 지점 위치 지도에 표시

In [14]:
for  lat , lng ,name in zip(hb['latitude'],hb['longitude'], hb['name']):
    mc.add_child(Marker(location = [lat, lng],popup= name))
    
    
m.add_child(mc)    

### 인구 데이터 지도 위에 색 명암으로 표시

In [15]:
pop = pd.read_csv('./data/pop.csv')

In [16]:
state_geo = './data/TL_SCCO_CTPRVN.json'
with open(state_geo,encoding = 'utf-8') as file:
    sido_map = json.load(file)

In [17]:
for i in range(0,17):
    print(sido_map['features'][i]['properties']['CTP_KOR_NM'])

강원도
경기도
경상남도
경상북도
광주광역시
대구광역시
대전광역시
부산광역시
서울특별시
세종특별자치시
울산광역시
인천광역시
전라남도
전라북도
제주특별자치도
충청남도
충청북도


In [18]:
pop.sort_values('시도별',inplace = True)
pop_2021 = pop[pop['year'] == 2021]

pop_2021['시도별'] = ['강원도',
'경기도',
'경상남도',
'경상북도',
'광주광역시',
'대구광역시',
'대전광역시',
'부산광역시',
'서울특별시',
'세종특별자치시',
'울산광역시',
'인천광역시',
'전라남도',
'전라북도',
'제주특별자치도',
'충청남도',
'충청북도']

C:\Users\icn97\AppData\Local\Temp\ipykernel_28440\1307596526.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pop_2021['시도별'] = ['강원도',


In [19]:
pop_2021

시도별   GRDP  year  1인당_사교육비(만 원)       인구수
111      강원도  21038  2021           28.9   1521890
110      경기도  21937  2021           42.2  13652529
117     경상남도  20650  2021           29.8   3305931
116     경상북도  20667  2021           31.6   2635314
106    광주광역시  22472  2021           37.4   1475262
104    대구광역시  21046  2021           42.2   2387911
107    대전광역시  22730  2021           35.3   1479740
103    부산광역시  21352  2021           42.1   3324335
102    서울특별시  25256  2021           52.6   9472127
109  세종특별자치시  22061  2021           40.6    366227
108    울산광역시  25165  2021           34.0   1120753
105    인천광역시  21317  2021           38.9   2957044
115     전라남도  20881  2021           25.6   1778124
114     전라북도  20862  2021           30.0   1787053
118  제주특별자치도  20475  2021           34.2    673107
113     충청남도  21262  2021           29.2   2175960
112     충청북도  21081  2021           28.7   1624764

In [20]:
ch = folium.Choropleth(
    geo_data=sido_map,
    name='choropleth',
    data=pop_2021,
    columns=['시도별','인구수'], 
    key_on='feature.properties.CTP_KOR_NM',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=1,
    line_weight=1.5,
    line_color='#000',
    legend_name='시도별 인구수(명)',  
).add_to(m)


m

In [56]:
m.save('map.html')

### 각 지점에서 초등학교까지의 거리에 차이가 있는지 t-test ( 두 점 사이의 거리 구하는 공식 사용 )

In [21]:
elementary = pd.read_csv('./data/elementary.csv')

In [22]:
school = pd.DataFrame()
school['latitude'] = elementary['위도']
school['longitude'] = elementary['경도']

In [83]:
min_hb_school = []

for i in range(len(hb)):
    
    list_cal = []
    
    for j in range(len(school)):
        
        
        x = (hb.loc[i,'latitude']-school.loc[j,'latitude'])**2 
        y = (hb.loc[i,'longitude']-school.loc[j,'longitude'])**2
        z = np.sqrt(x+y)
        
        list_cal.append(z)
        
    min_hb_school.append(min(list_cal))

In [91]:
min_competitor_school = []

for i in range(len(competitor)):
    
    list_cal = []
    
    for j in range(len(school)):
        
        
        x = (competitor.loc[i,'latitude']-school.loc[j,'latitude'])**2 
        y = (competitor.loc[i,'longitude']-school.loc[j,'longitude'])**2
        z = np.sqrt(x+y)
        
        list_cal.append(z)
        
    min_competitor_school.append(min(list_cal))

In [141]:
t_stat, p_val = stats.ttest_ind(min_hb_school, min_competitor_school)

Ttest_indResult(statistic=0.537360869425262, pvalue=0.5910592150105263)

In [93]:
print(t_stat,p_val)

0.537360869425262 0.5910592150105263


### 각 지점에서 초등학교까지의 거리에 차이가 있는지 t-test ( 하버사인 공식 사용 )

In [96]:
min_hb_school_hs = []

for i in range(len(hb)):
    
    list_cal = []
    
    loc1 = (hb.loc[i,'latitude'],hb.loc[i,'longitude'])
    
    for j in range(len(school)):
        
        
        loc2 = (school.loc[i,'latitude'],school.loc[i,'longitude'])
        haver = hs.haversine(loc1,loc2, unit = 'km')
        
        list_cal.append(haver)
        
    min_hb_school_hs.append(min(list_cal))

In [97]:
min_competitor_school_hs = []

for i in range(len(competitor)):
    
    list_cal = []
    
    loc1 = (competitor.loc[i,'latitude'],competitor.loc[i,'longitude'])
    
    for j in range(len(school)):
        
        
        loc2 = (school.loc[i,'latitude'],school.loc[i,'longitude'])
        haver = hs.haversine(loc1,loc2, unit = 'km')
        
        list_cal.append(haver)
        
    min_competitor_school_hs.append(min(list_cal))

In [105]:
min_hb_school_hs = pd.DataFrame(min_hb_school_hs).dropna(axis = 0)

In [114]:
min_hb_school_hs = min_hb_school_hs[0].to_list()

In [140]:
t_stat, p_val = stats.ttest_ind(min_hb_school_hs,min_competitor_school_hs)

Ttest_indResult(statistic=-0.12683361932218112, pvalue=0.8990808100115038)

In [116]:
print(t_stat, p_val)

-0.12683361932218112 0.8990808100115038
